In [ ]:
#https://machinelearningmastery.com/sequence-classification-lstm-recurrent-neural-networks-python-keras/
#https://machinelearningmastery.com/text-generation-lstm-recurrent-neural-networks-python-keras/

In [1]:
import numpy as np
from keras.models import Sequential
from keras.layers import Dense
from keras.layers import Dropout
from keras.layers import LSTM
from keras.callbacks import ModelCheckpoint
from keras.utils import np_utils

import glob
import sys

Using TensorFlow backend.


In [2]:
n=-1
dir_ = 'playlists/country/'
files = glob.glob('%s*.txt'%dir_)[0:n]

In [3]:
def unicodetoascii(text):
    TEXT = (text.
            replace('\xe2\x80\x99', "'").
            replace('\xe2\x80\x8be', 'e').
            replace('\xc3\xa9', 'e').
            replace('\xc2\x92',"'").
            replace('\xe2\x80\x90', '-').
            replace('\xe2\x80\x91', '-').
            replace('\xe2\x80\x92', '-').
            replace('\xe2\x80\x93', '-').
            replace('\xe2\x80\x94', '-').
            replace('\xe2\x80\x94', '-').
            replace('\xe2\x80\x98', "'").
            replace('\xe2\x80\x9b', "'").
            replace('\xe2\x80\x9c', '"').
            replace('\xe2\x80\x9c', '"').
            replace('\xe2\x80\x9d', '"').
            replace('\xe2\x80\x9e', '"').
            replace('\xe2\x80\x9f', '"').
            replace('\xe2\x80\xa6', '...').
            replace('\xe2\x80\xb2', "'").
            replace('\xe2\x80\xb3', "'").
            replace('\xe2\x80\xb4', "'").
            replace('\xe2\x80\xb5', "'").
            replace('\xe2\x80\xb6', "'").
            replace('\xe2\x80\xb7', "'").
            replace('\xe2\x81\xba', "+").
            replace('\xe2\x81\xbb', "-").
            replace('\xe2\x81\xbc', "=").
            replace('\xe2\x81\xbd', "(").
            replace('\xe2\x81\xbe', ")").
            replace('\xe2\x80\x8b', '').
            replace('\xc3\xa2\xe2\x82\xac\xcb\x9c',"'").
            replace('\xc3\xa0','a').
            replace('\xc3\xa4','a').
            replace('\xc3\xb1','n').
            replace('\xc3\xb3','o').
            replace('_',' ').
            replace('*',' ').
            replace('+','and').
            replace('{','[').
            replace('}',']').
            replace('`',"'").
            replace('"',"'").
            replace('$','').
            replace('&','and').
            replace('/',' and ')
                 )
    return TEXT

def process_song(song_dir):
    song = unicodetoascii(open(song_dir,'r').read().lower())
    return song

In [166]:
i=1059
print files[i]
song = unicodetoascii(open(files[i],'r').read().lower())
song

playlists/country/Luke_Bryan-Kick_The_Dust_Up.txt


"\n\nkick the dust up, c'mon\n\n[verse 1]\nall week long it's a farmin' town\nthey're makin' that money grow\ntractors, plows with flashing lights\nbackin' up a two lane road\nthey take one last lap around\nthat sun up high goes down\nand then it's on, come on\ngirl kick it on back\nz71 like a cadillac\n\n[chorus]\nwe go way out where\nthere ain't nobody\nwe turn this cornfield\ninto a party\npedal to the floorboard\neight up in a four door\nburnin' up a back road song\npark it and we pile out\nbaby, watch your step now\nbetter have your boots on\nkick the dust up\nback it on up\nfill your cup up\nlet's tear it up, up\nand kick the dust up (kick the dust up...)\n\n[verse 2]\nbar downtown they got a line\nof people way out the door\n10 dollar drinks, it's packed inside\ni don't know what they're waitin for\ngot me a jar full of clear\nand i got that music for your ears\nand it's like knock, knock, knock goes the diesel\nif you really wanna see the beautiful people\n\n[chorus]\nwe go way

In [4]:
songs = []
for i,f in enumerate(files):
#    song = unicodetoascii(open(f,'r').read().lower())
#     if '$' in song:
#         print i
    songs.append(process_song(f))

In [5]:
chars = sorted(list(set(' '.join(songs))))
char_to_int = dict((c, i) for i, c in enumerate(chars))
char_to_int

{'\n': 0,
 ' ': 1,
 '!': 2,
 "'": 3,
 '(': 4,
 ')': 5,
 ',': 6,
 '-': 7,
 '.': 8,
 '0': 9,
 '1': 10,
 '2': 11,
 '3': 12,
 '4': 13,
 '5': 14,
 '6': 15,
 '7': 16,
 '8': 17,
 '9': 18,
 ':': 19,
 ';': 20,
 '?': 21,
 '[': 22,
 ']': 23,
 'a': 24,
 'b': 25,
 'c': 26,
 'd': 27,
 'e': 28,
 'f': 29,
 'g': 30,
 'h': 31,
 'i': 32,
 'j': 33,
 'k': 34,
 'l': 35,
 'm': 36,
 'n': 37,
 'o': 38,
 'p': 39,
 'q': 40,
 'r': 41,
 's': 42,
 't': 43,
 'u': 44,
 'v': 45,
 'w': 46,
 'x': 47,
 'y': 48,
 'z': 49}

In [24]:
seq_length = 30
dataX = []
dataY = []
for i in range(100):
    song_text = songs[i]
    for j in range(0,len(song_text)-seq_length, 1):
        seq_in = song_text[j:j + seq_length]
        seq_out = song_text[j + seq_length]
        #print repr(seq_in),"<<>>", repr(seq_out)
        dataX.append([char_to_int[char] for char in seq_in])
        dataY.append(char_to_int[seq_out])
n_patterns = len(dataX)
print "Total Patterns: ", n_patterns

'\n\nday one\ni stumbled through h' <<>> 'e'
'\nday one\ni stumbled through he' <<>> 'l'
'day one\ni stumbled through hel' <<>> 'l'
'ay one\ni stumbled through hell' <<>> 'o'
'y one\ni stumbled through hello' <<>> ' '
' one\ni stumbled through hello ' <<>> 'o'
'one\ni stumbled through hello o' <<>> 'n'
'ne\ni stumbled through hello on' <<>> ' '
'e\ni stumbled through hello on ' <<>> '5'
'\ni stumbled through hello on 5' <<>> 't'
'i stumbled through hello on 5t' <<>> 'h'
' stumbled through hello on 5th' <<>> ' '
'stumbled through hello on 5th ' <<>> 'a'
'tumbled through hello on 5th a' <<>> 'v'
'umbled through hello on 5th av' <<>> 'e'
'mbled through hello on 5th ave' <<>> 'n'
'bled through hello on 5th aven' <<>> 'u'
'led through hello on 5th avenu' <<>> 'e'
'ed through hello on 5th avenue' <<>> '\n'
'd through hello on 5th avenue\n' <<>> 'd'
' through hello on 5th avenue\nd' <<>> 'a'
'through hello on 5th avenue\nda' <<>> 'y'
'hrough hello on 5th avenue\nday' <<>> ' '
'rough hello on 

'\n\nwhat a beautiful day\nwhat a ' <<>> 'b'
'\nwhat a beautiful day\nwhat a b' <<>> 'e'
'what a beautiful day\nwhat a be' <<>> 'a'
'hat a beautiful day\nwhat a bea' <<>> 'u'
'at a beautiful day\nwhat a beau' <<>> 't'
't a beautiful day\nwhat a beaut' <<>> 'i'
' a beautiful day\nwhat a beauti' <<>> 'f'
'a beautiful day\nwhat a beautif' <<>> 'u'
' beautiful day\nwhat a beautifu' <<>> 'l'
'beautiful day\nwhat a beautiful' <<>> ' '
'eautiful day\nwhat a beautiful ' <<>> 'd'
'autiful day\nwhat a beautiful d' <<>> 'a'
'utiful day\nwhat a beautiful da' <<>> 'y'
'tiful day\nwhat a beautiful day' <<>> '\n'
'iful day\nwhat a beautiful day\n' <<>> '\n'
'ful day\nwhat a beautiful day\n\n' <<>> 'd'
'ul day\nwhat a beautiful day\n\nd' <<>> 'a'
'l day\nwhat a beautiful day\n\nda' <<>> 'y'
' day\nwhat a beautiful day\n\nday' <<>> ' '
'day\nwhat a beautiful day\n\nday ' <<>> 'o'
'ay\nwhat a beautiful day\n\nday o' <<>> 'n'
'y\nwhat a beautiful day\n\nday on' <<>> 'e'
'\nwhat a beautiful day\n\nday one

'wing...\nooh we had our ups and' <<>> ' '
'ing...\nooh we had our ups and ' <<>> 'd'
'ng...\nooh we had our ups and d' <<>> 'o'
'g...\nooh we had our ups and do' <<>> 'w'
'...\nooh we had our ups and dow' <<>> 'n'
'..\nooh we had our ups and down' <<>> 's'
'.\nooh we had our ups and downs' <<>> '\n'
'\nooh we had our ups and downs\n' <<>> 'a'
'ooh we had our ups and downs\na' <<>> 'l'
'oh we had our ups and downs\nal' <<>> 'l'
'h we had our ups and downs\nall' <<>> ' '
' we had our ups and downs\nall ' <<>> 'a'
'we had our ups and downs\nall a' <<>> 'l'
'e had our ups and downs\nall al' <<>> 'o'
' had our ups and downs\nall alo' <<>> 'n'
'had our ups and downs\nall alon' <<>> 'g'
'ad our ups and downs\nall along' <<>> ' '
'd our ups and downs\nall along ' <<>> 't'
' our ups and downs\nall along t' <<>> 'h'
'our ups and downs\nall along th' <<>> 'e'
'ur ups and downs\nall along the' <<>> ' '
'r ups and downs\nall along the ' <<>> 'w'
' ups and downs\nall along the w' <<>> 'a'
'ups and 

' it would probably be his last' <<>> '\n'
'it would probably be his last\n' <<>> 'h'
't would probably be his last\nh' <<>> 'e'
' would probably be his last\nhe' <<>> ' '
'would probably be his last\nhe ' <<>> 'w'
'ould probably be his last\nhe w' <<>> 'a'
'uld probably be his last\nhe wa' <<>> 's'
'ld probably be his last\nhe was' <<>> ' '
'd probably be his last\nhe was ' <<>> 'c'
' probably be his last\nhe was c' <<>> 'r'
'probably be his last\nhe was cr' <<>> 'a'
'robably be his last\nhe was cra' <<>> 'c'
'obably be his last\nhe was crac' <<>> 'k'
'bably be his last\nhe was crack' <<>> 'i'
'ably be his last\nhe was cracki' <<>> 'n'
'bly be his last\nhe was crackin' <<>> ' '
'ly be his last\nhe was crackin ' <<>> 'j'
'y be his last\nhe was crackin j' <<>> 'o'
' be his last\nhe was crackin jo' <<>> 'k'
'be his last\nhe was crackin jok' <<>> 'e'
'e his last\nhe was crackin joke' <<>> 's'
' his last\nhe was crackin jokes' <<>> ' '
'his last\nhe was crackin jokes ' <<>> 'a'
'is last\nh

'vin, goin crazy in the kitchen' <<>> '\n'
'in, goin crazy in the kitchen\n' <<>> 'w'
'n, goin crazy in the kitchen\nw' <<>> 'e'
', goin crazy in the kitchen\nwe' <<>> ' '
' goin crazy in the kitchen\nwe ' <<>> 'd'
'goin crazy in the kitchen\nwe d' <<>> 'a'
'oin crazy in the kitchen\nwe da' <<>> 'n'
'in crazy in the kitchen\nwe dan' <<>> 'c'
'n crazy in the kitchen\nwe danc' <<>> 'e'
' crazy in the kitchen\nwe dance' <<>> 'd'
'crazy in the kitchen\nwe danced' <<>> ' '
'razy in the kitchen\nwe danced ' <<>> 'a'
'azy in the kitchen\nwe danced a' <<>> 'n'
'zy in the kitchen\nwe danced an' <<>> 'd'
'y in the kitchen\nwe danced and' <<>> ' '
' in the kitchen\nwe danced and ' <<>> 's'
'in the kitchen\nwe danced and s' <<>> 'c'
'n the kitchen\nwe danced and sc' <<>> 'r'
' the kitchen\nwe danced and scr' <<>> 'e'
'the kitchen\nwe danced and scre' <<>> 'a'
'he kitchen\nwe danced and screa' <<>> 'm'
'e kitchen\nwe danced and scream' <<>> 'e'
' kitchen\nwe danced and screame' <<>> 'd'
'kitchen\nw

...

'hink the world needs a drink\nd' <<>> 'o'
'ink the world needs a drink\ndo' <<>> 'n'
'nk the world needs a drink\ndon' <<>> 't'
'k the world needs a drink\ndont' <<>> ' '
' the world needs a drink\ndont ' <<>> 'y'
'the world needs a drink\ndont y' <<>> 'o'
'he world needs a drink\ndont yo' <<>> 'u'
'e world needs a drink\ndont you' <<>> ' '
' world needs a drink\ndont you ' <<>> 't'
'world needs a drink\ndont you t' <<>> 'h'
'orld needs a drink\ndont you th' <<>> 'i'
'rld needs a drink\ndont you thi' <<>> 'n'
'ld needs a drink\ndont you thin' <<>> 'k'
'd needs a drink\ndont you think' <<>> ' '
' needs a drink\ndont you think ' <<>> 't'
'needs a drink\ndont you think t' <<>> 'h'
'eeds a drink\ndont you think th' <<>> 'e'
'eds a drink\ndont you think the' <<>> ' '
'ds a drink\ndont you think the ' <<>> 'w'
's a drink\ndont you think the w' <<>> 'o'
' a drink\ndont you think the wo' <<>> 'r'
'a drink\ndont you think the wor' <<>> 'l'
' drink\ndont you think the worl' <<>> 'd'
'drink\ndon

'l those pretty blue eyes\nlaugh' <<>> ' '
' those pretty blue eyes\nlaugh ' <<>> 'a'
'those pretty blue eyes\nlaugh a' <<>> 'n'
'hose pretty blue eyes\nlaugh an' <<>> 'd'
'ose pretty blue eyes\nlaugh and' <<>> ' '
'se pretty blue eyes\nlaugh and ' <<>> 's'
'e pretty blue eyes\nlaugh and s' <<>> 'a'
' pretty blue eyes\nlaugh and sa' <<>> 'y'
'pretty blue eyes\nlaugh and say' <<>> ' '
'retty blue eyes\nlaugh and say ' <<>> 'b'
'etty blue eyes\nlaugh and say b' <<>> 'o'
'tty blue eyes\nlaugh and say bo' <<>> 'y'
'ty blue eyes\nlaugh and say boy' <<>> ' '
'y blue eyes\nlaugh and say boy ' <<>> 'y'
' blue eyes\nlaugh and say boy y' <<>> 'o'
'blue eyes\nlaugh and say boy yo' <<>> 'u'
'lue eyes\nlaugh and say boy you' <<>> ' '
'ue eyes\nlaugh and say boy you ' <<>> 'l'
'e eyes\nlaugh and say boy you l' <<>> 'i'
' eyes\nlaugh and say boy you li' <<>> 'e'
'eyes\nlaugh and say boy you lie' <<>> ','
'yes\nlaugh and say boy you lie,' <<>> ' '
'es\nlaugh and say boy you lie, ' <<>> 'g'
's\nlaugh a

'to go to heaven\nif they wouldn' <<>> "'"
"o go to heaven\nif they wouldn'" <<>> 't'
" go to heaven\nif they wouldn't" <<>> ' '
"go to heaven\nif they wouldn't " <<>> 'l'
"o to heaven\nif they wouldn't l" <<>> 'e'
" to heaven\nif they wouldn't le" <<>> 't'
"to heaven\nif they wouldn't let" <<>> ' '
"o heaven\nif they wouldn't let " <<>> 'm'
" heaven\nif they wouldn't let m" <<>> 'e'
"heaven\nif they wouldn't let me" <<>> ' '
"eaven\nif they wouldn't let me " <<>> 'i'
"aven\nif they wouldn't let me i" <<>> 'n'
"ven\nif they wouldn't let me in" <<>> '\n'
"en\nif they wouldn't let me in\n" <<>> 'i'
"n\nif they wouldn't let me in\ni" <<>> "'"
"\nif they wouldn't let me in\ni'" <<>> 'd'
"if they wouldn't let me in\ni'd" <<>> ' '
"f they wouldn't let me in\ni'd " <<>> 'b'
" they wouldn't let me in\ni'd b" <<>> 'r'
"they wouldn't let me in\ni'd br" <<>> 'e'
"hey wouldn't let me in\ni'd bre" <<>> 'a'
"ey wouldn't let me in\ni'd brea" <<>> 'k'
"y wouldn't let me in\ni'd break" <<>> ' '
" would

'okin back at you from the cove' <<>> 'r'
'kin back at you from the cover' <<>> ' '
'in back at you from the cover ' <<>> 'o'
'n back at you from the cover o' <<>> 'f'
' back at you from the cover of' <<>> ' '
'back at you from the cover of ' <<>> 'a'
'ack at you from the cover of a' <<>> ' '
'ck at you from the cover of a ' <<>> 'p'
'k at you from the cover of a p' <<>> 'e'
' at you from the cover of a pe' <<>> 'o'
'at you from the cover of a peo' <<>> 'p'
't you from the cover of a peop' <<>> 'l'
' you from the cover of a peopl' <<>> 'e'
'you from the cover of a people' <<>> ' '
'ou from the cover of a people ' <<>> 'm'
'u from the cover of a people m' <<>> 'a'
' from the cover of a people ma' <<>> 'g'
'from the cover of a people mag' <<>> 'a'
'rom the cover of a people maga' <<>> 'z'
'om the cover of a people magaz' <<>> 'i'
'm the cover of a people magazi' <<>> 'n'
' the cover of a people magazin' <<>> 'e'
'the cover of a people magazine' <<>> '\n'
'he cover of a people magazine\n'

KeyboardInterrupt: 

In [8]:
# reshape X to be [samples, time steps, features]
X = np.reshape(dataX, (n_patterns, seq_length, 1))
# normalize
X = X / float(len(chars))
# one hot encode the output variable
y = np_utils.to_categorical(dataY)

In [9]:
model = Sequential()
model.add(LSTM(256, input_shape=(X.shape[1], X.shape[2])))
model.add(Dropout(0.2))
model.add(Dense(y.shape[1], activation='softmax'))
model.compile(loss='categorical_crossentropy', optimizer='adam')

In [10]:
model.fit(X, y, epochs=2, batch_size=128)#, callbacks=callbacks_list)

Epoch 1/2
138863/138863 [==============================] - 294s - loss: 2.9543   
Epoch 2/2
138863/138863 [==============================] - 294s - loss: 2.7513   


In [11]:
int_to_char = dict((i, c) for i, c in enumerate(chars))

In [56]:
start = np.random.randint(0, len(dataX)-1)
pattern = dataX[start]

In [57]:
print "\"", ''.join([int_to_char[value] for value in pattern]), "\""

" at right
he said, they won't s "


In [61]:
lyric = [int_to_char[value] for value in pattern]

for i in range(100):
    x = np.reshape(pattern, (1, len(pattern), 1))
    x = x / float(len(chars))
    prediction = model.predict(x, verbose=0)
    index = np.argmax(prediction)
    result = int_to_char[index]
    seq_in = [int_to_char[value] for value in pattern]
    #sys.stdout.write(result)
    lyric.append(result)
    pattern.append(index)
    pattern = pattern[1:len(pattern)]

In [62]:
''.join(lyric)

"t right\nhe said, they won't sone to tee toe toe toe toe toe toe toe toe toe toe toe toe toe toe toe toe toe toe toe toe toe toe to"